# Plot H2

This file visualizes the main findings for the H2 hypothesis.

In [1]:
import sys
import os.path as op
module_path = op.abspath(op.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

from scipy.io import loadmat
import hypyp
import mne
import numpy as np

from data_analysis.functions_connectivity import \
    plot_connectivity_matrix
from data_analysis.functions_behavioral import \
    (create_event_df, remove_ghost_triggers, calculate_alpha,
     join_event_dfs, remove_outliers, events_from_event_df)

import matplotlib.pyplot as plt
from matplotlib.lines import Line2D


result_dir = "/net/store/nbp/projects/hyperscanning/study_project/results/"

p_blue = '#2f77b4'
p_yellow = '#ff7f0e'
p_green = '#2ca02c'
p_red = '#d62728'

In /net/store/nbp/projects/hyperscanning/study_project/programming_tools/miniconda3/envs/hyperscanning/lib/python3.8/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: 
The text.latex.preview rcparam was deprecated in Matplotlib 3.3 and will be removed two minor releases later.
In /net/store/nbp/projects/hyperscanning/study_project/programming_tools/miniconda3/envs/hyperscanning/lib/python3.8/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: 
The mathtext.fallback_to_cm rcparam was deprecated in Matplotlib 3.3 and will be removed two minor releases later.
In /net/store/nbp/projects/hyperscanning/study_project/programming_tools/miniconda3/envs/hyperscanning/lib/python3.8/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: Support for setting the 'mathtext.fallback_to_cm' rcParam is deprecated since 3.3 and will be removed two minor releases later; use 'mathtext.fallback : 'cm' instead.
In /net/store/nbp/projects/hyperscanning/study_project

In [2]:
# get frequency bands (from any subject)
cond = "early"
tfr = mne.time_frequency.read_tfrs(op.join(result_dir, "phase_angles", "202" + "_" + cond))[0]

Reading /net/store/nbp/projects/hyperscanning/study_project/results/phase_angles/202_early ...


<ipython-input-2-858ff87733f8>:3: RuntimeWarning: This filename (/net/store/nbp/projects/hyperscanning/study_project/results/phase_angles/202_early) does not conform to MNE naming conventions. All tfr files should end with -tfr.h5 or _tfr.h5
  tfr = mne.time_frequency.read_tfrs(op.join(result_dir, "phase_angles", "202" + "_" + cond))[0]


Not setting metadata


## Early ISPC

In [3]:
plt.figure(figsize=(10,6),dpi=1200)

pair = '202'
cond = "early"
ispcs_early = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]

for pair in ['203','204','205','206','207','208','209','211','212']:
    ispcs_pair = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    ispcs_early = np.concatenate((ispcs_early,ispcs_pair)) 

# get avg over pairs             
avg_ispcs_early = np.mean(ispcs_early, axis=0)
inter_early = [np.mean(avg_ispcs_early[0:64, 64:2*64, i]) for i in range(avg_ispcs_early.shape[2])]
intra_early = [np.mean(avg_ispcs_early[0:64, 0:64, i]) for i in range(avg_ispcs_early.shape[2])]

# plot
plt.plot(tfr.freqs, inter_early, c=p_blue, ls='--') 
plt.plot(tfr.freqs, intra_early, c=p_blue)

# cosmetics
plt.legend(["inter", "intra"])
plt.title('Early ISPCS of all pairs and all trials')
plt.ylim(0,.6)
plt.xlabel('frequency')
plt.ylabel('ISPC')  

# log scale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

print(f'Mean ISPC(inter) = {round(np.mean(inter_early),5)}')
print(f'standard deviation = {round(np.std(inter_early),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_early),5)} @ freq {round(tfr.freqs[np.argmax(inter_early)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_early),5)}')
print(f'standard deviation = {round(np.std(intra_early),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_early),5)} @ freq {round(tfr.freqs[np.argmax(intra_early)],2)}')
print()

Mean ISPC(inter) = 0.25867
standard deviation = 0.00507
Peak ISPC(inter) 0.27299 @ freq 4.0

Mean ISPC(intra) = 0.47708
standard deviation = 0.02333
Peak ISPC(intra) 0.51294 @ freq 4.0



In [4]:
plt.figure(figsize=(10,6),dpi=1200)
for pair in ['202','203','204','205','206','207','208','209','211','212']:
    cond = "early"
    ispcs_early_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    avg_ispcs_early_pairs = np.mean(ispcs_early_pairs, axis=0)

    inter_early_pairs = [np.mean(avg_ispcs_early_pairs[0:64, 64:2*64, i]) for i in range(avg_ispcs_early_pairs.shape[2])]
    intra_early_pairs = [np.mean(avg_ispcs_early_pairs[0:64, 0:64, i]) for i in range(avg_ispcs_early_pairs.shape[2])]
    
    print(f'Pair{pair}: Mean ISPC(inter) = {round(np.mean(inter_early_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(inter_early_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(inter) {round(np.max(inter_early_pairs),5)} @ freq {round(tfr.freqs[np.argmax(inter_early_pairs)],2)}')
    print()
    
    print(f'Pair{pair}: Mean ISPC(intra) = {round(np.mean(intra_early_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(intra_early_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(intra) {round(np.max(intra_early_pairs),5)} @ freq {round(tfr.freqs[np.argmax(intra_early_pairs)],2)}')
    print()
    
    # plot
    plt.plot(tfr.freqs, inter_early_pairs, alpha=0.4, ls='--') 
    plt.plot(tfr.freqs, intra_early_pairs, alpha=0.4)
    plt.xticks([],visible=False)


# plot means:
plt.plot(tfr.freqs, inter_early, lw=3, c=p_blue, ls='--') 
plt.plot(tfr.freqs, intra_early, lw=3, c=p_blue)

    
# cosmetics
plt.title('Early ISPCS of each pair over all trials')
plt.ylim(0,.6)
plt.xlabel('frequency')
plt.ylabel('ISPC')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

# legendworkaround
custom_lines = [Line2D([0], [0], color='k', lw=1, ls='--'),
                Line2D([0], [0], color='k', lw=1, ls='-'),
                Line2D([0], [0], color=p_blue, lw=2.5, ls='-')]
plt.legend(custom_lines,['interbrain','intrabrain','mean'])

plt.show()
print(f'Mean ISPC(inter) = {round(np.mean(inter_early),5)}')
print(f'standard deviation = {round(np.std(inter_early),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_early),5)} @ freq {round(tfr.freqs[np.argmax(inter_early)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_early),5)}')
print(f'standard deviation = {round(np.std(intra_early),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_early),5)} @ freq {round(tfr.freqs[np.argmax(intra_early)],2)}')
print()

Pair202: Mean ISPC(inter) = 0.25847
Pair202: standard deviation = 0.0061
Pair202: Peak ISPC(inter) 0.27346 @ freq 4.0

Pair202: Mean ISPC(intra) = 0.47125
Pair202: standard deviation = 0.02402
Pair202: Peak ISPC(intra) 0.51701 @ freq 8.59

Pair203: Mean ISPC(inter) = 0.26003
Pair203: standard deviation = 0.0084
Pair203: Peak ISPC(inter) 0.27615 @ freq 11.08

Pair203: Mean ISPC(intra) = 0.48152
Pair203: standard deviation = 0.0291
Pair203: Peak ISPC(intra) 0.53788 @ freq 4.0

Pair204: Mean ISPC(inter) = 0.25847
Pair204: standard deviation = 0.00616
Pair204: Peak ISPC(inter) 0.27755 @ freq 4.0

Pair204: Mean ISPC(intra) = 0.47772
Pair204: standard deviation = 0.02284
Pair204: Peak ISPC(intra) 0.51194 @ freq 8.59

Pair205: Mean ISPC(inter) = 0.26109
Pair205: standard deviation = 0.00793
Pair205: Peak ISPC(inter) 0.28045 @ freq 4.0

Pair205: Mean ISPC(intra) = 0.4865
Pair205: standard deviation = 0.02242
Pair205: Peak ISPC(intra) 0.52078 @ freq 6.66

Pair206: Mean ISPC(inter) = 0.26019
Pai

Mean ISPC(inter) = 0.25867
standard deviation = 0.00507
Peak ISPC(inter) 0.27299 @ freq 4.0

Mean ISPC(intra) = 0.47708
standard deviation = 0.02333
Peak ISPC(intra) 0.51294 @ freq 4.0



## Late ISPC

In [5]:
plt.figure(figsize=(10,6),dpi=1200)
pair = '202'
cond = "late"
ispcs_late = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
#tfr_late = mne.time_frequency.read_tfrs(op.join(result_dir, "phase_angles", str(pair) + "_" + cond))[0]

for pair in ['203','204','205','206','207','208','209','211','212']:
    ispcs_pair = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    ispcs_late = np.concatenate((ispcs_late,ispcs_pair)) 

             
avg_ispcs_late = np.mean(ispcs_late, axis=0)
inter_late = [np.mean(avg_ispcs_late[0:64, 64:2*64, i]) for i in range(avg_ispcs_late.shape[2])]
intra_late = [np.mean(avg_ispcs_late[0:64, 0:64, i]) for i in range(avg_ispcs_late.shape[2])]

# plot
plt.plot(tfr.freqs, inter_late, c=p_yellow, ls='--')
plt.plot(tfr.freqs, intra_late, c=p_yellow)

# cosmetics
plt.legend(["inter", "intra"])
plt.title('Late ISPCS of all pairs and all trials')
plt.ylim(0,.6)
plt.xlabel('frequency')
plt.ylabel('ISPC')  

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()
print(f'Mean ISPC(inter) = {round(np.mean(inter_late),5)}')
print(f'standard deviation = {round(np.std(inter_late),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_late),5)} @ freq {round(tfr.freqs[np.argmax(inter_late)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_late),5)}')
print(f'standard deviation = {round(np.std(intra_late),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_late),5)} @ freq {round(tfr.freqs[np.argmax(intra_late)],2)}')
print()

Mean ISPC(inter) = 0.25711
standard deviation = 0.00385
Peak ISPC(inter) 0.26852 @ freq 4.0

Mean ISPC(intra) = 0.47511
standard deviation = 0.02228
Peak ISPC(intra) 0.50935 @ freq 4.0



In [6]:
plt.figure(figsize=(10,6),dpi=1200)

for pair in ['202','203','204','205','206','207','208','209','211','212']:
    cond = "late"
    ispcs_late_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    avg_ispcs_late_pairs = np.mean(ispcs_late_pairs, axis=0)
    
    inter_late_pairs = [np.mean(avg_ispcs_late_pairs[0:64, 64:2*64, i]) for i in range(avg_ispcs_late_pairs.shape[2])]
    intra_late_pairs = [np.mean(avg_ispcs_late_pairs[0:64, 0:64, i]) for i in range(avg_ispcs_late_pairs.shape[2])]
    
    print(f'Pair{pair}: Mean ISPC(inter) = {round(np.mean(inter_late_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(inter_late_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(inter) {round(np.max(inter_late_pairs),5)} @ freq {round(tfr.freqs[np.argmax(inter_late_pairs)],2)}')
    print()
    
    print(f'Pair{pair}: Mean ISPC(intra) = {round(np.mean(intra_late_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(intra_late_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(intra) {round(np.max(intra_late_pairs),5)} @ freq {round(tfr.freqs[np.argmax(intra_late_pairs)],2)}')
    print()
    
    
    # plot
    plt.plot(tfr.freqs, inter_late_pairs, alpha=0.4, ls='--')
    plt.plot(tfr.freqs, intra_late_pairs, alpha=0.4)

    
# plot means
plt.plot(tfr.freqs, inter_late, lw=3, c=p_yellow, ls='--')
plt.plot(tfr.freqs, intra_late, lw=3, c=p_yellow)

# plot cosmetics
plt.title('Late ISPCS of each pair over all trials')
plt.ylim(0,.6)
plt.xlabel('frequency')
plt.ylabel('ISPC')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])


# legendworkaround
custom_lines = [Line2D([0], [0], color='k', lw=1, ls='--'),
                Line2D([0], [0], color='k', lw=1, ls='-'),
                Line2D([0], [0], color=p_yellow, lw=2.5, ls='-')]
plt.legend(custom_lines,['interbrain','intrabrain','mean'])

plt.show()

print(f'Mean ISPC(inter) = {round(np.mean(inter_late),5)}')
print(f'standard deviation = {round(np.std(inter_late),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_late),5)} @ freq {round(tfr.freqs[np.argmax(inter_late)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_late),5)}')
print(f'standard deviation = {round(np.std(intra_late),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_late),5)} @ freq {round(tfr.freqs[np.argmax(intra_late)],2)}')
print()

Pair202: Mean ISPC(inter) = 0.25789
Pair202: standard deviation = 0.00505
Pair202: Peak ISPC(inter) 0.27041 @ freq 9.76

Pair202: Mean ISPC(intra) = 0.46914
Pair202: standard deviation = 0.02353
Pair202: Peak ISPC(intra) 0.51154 @ freq 8.59

Pair203: Mean ISPC(inter) = 0.25839
Pair203: standard deviation = 0.00701
Pair203: Peak ISPC(inter) 0.27494 @ freq 11.08

Pair203: Mean ISPC(intra) = 0.47911
Pair203: standard deviation = 0.03038
Pair203: Peak ISPC(intra) 0.53412 @ freq 4.0

Pair204: Mean ISPC(inter) = 0.25632
Pair204: standard deviation = 0.00375
Pair204: Peak ISPC(inter) 0.26898 @ freq 4.0

Pair204: Mean ISPC(intra) = 0.47938
Pair204: standard deviation = 0.0254
Pair204: Peak ISPC(intra) 0.51692 @ freq 8.59

Pair205: Mean ISPC(inter) = 0.25652
Pair205: standard deviation = 0.00762
Pair205: Peak ISPC(inter) 0.27794 @ freq 4.0

Pair205: Mean ISPC(intra) = 0.48895
Pair205: standard deviation = 0.02313
Pair205: Peak ISPC(intra) 0.52149 @ freq 4.0

Pair206: Mean ISPC(inter) = 0.25926


Mean ISPC(inter) = 0.25711
standard deviation = 0.00385
Peak ISPC(inter) 0.26852 @ freq 4.0

Mean ISPC(intra) = 0.47511
standard deviation = 0.02228
Peak ISPC(intra) 0.50935 @ freq 4.0



## ISPC early and late

In [7]:
plt.figure(figsize=(10,6),dpi=1200)

for pair in ['202','203','204','205','206','207','208','209','211','212']:
    cond = "late"
    ispcs_late_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    cond = "early"
    ispcs_early_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_" + cond + ".mat"))[cond]
    
    # concatenate both conditions and take avg over trials
    ispcs_pairs = np.concatenate((ispcs_early_pairs,ispcs_late_pairs), axis=0)
    avg_ispcs_pairs = np.mean(ispcs_pairs, axis=0)
    
    inter_pairs = [np.mean(avg_ispcs_pairs[0:64, 64:2*64, i]) for i in range(avg_ispcs_pairs.shape[2])]
    intra_pairs = [np.mean(avg_ispcs_pairs[0:64, 0:64, i]) for i in range(avg_ispcs_pairs.shape[2])]
    
    print(f'Pair{pair}: Mean ISPC(inter) = {round(np.mean(inter_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(inter_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(inter) {round(np.max(inter_pairs),5)} @ freq {round(tfr.freqs[np.argmax(inter_pairs)],2)}')
    print()
    
    print(f'Pair{pair}: Mean ISPC(intra) = {round(np.mean(intra_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(intra_pairs),5)}')
    print(f'Pair{pair}: Peak ISPC(intra) {round(np.max(intra_pairs),5)} @ freq {round(tfr.freqs[np.argmax(intra_pairs)],2)}')
    print()
    
    
    # plot
    plt.plot(tfr.freqs, inter_pairs, alpha=0.4, ls='--')
    plt.plot(tfr.freqs, intra_pairs, alpha=0.4)

    
# plot means
inter_all = [(x+y)/2 for x,y in zip(inter_early,inter_late)]
intra_all = [(x+y)/2 for x,y in zip(intra_early,intra_late)]

plt.plot(tfr.freqs, inter_all, lw=3, c='g', ls='--')
plt.plot(tfr.freqs, intra_all, lw=3, c='g')

# plot cosmetics
plt.title('ISPCS of each pair over all trials')
plt.ylim(0,.6)
plt.xlabel('frequency')
plt.ylabel('ISPC')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])


# legendworkaround
custom_lines = [Line2D([0], [0], color='k', lw=1, ls='--'),
                Line2D([0], [0], color='k', lw=1, ls='-'),
                Line2D([0], [0], color='g', lw=3, ls='-')]
plt.legend(custom_lines,['interbrain','intrabrain','mean'])

plt.show()

print(f'Mean ISPC(inter) = {round(np.mean(inter_all),5)}')
print(f'standard deviation = {round(np.std(inter_all),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_all),5)} @ freq {round(tfr.freqs[np.argmax(inter_all)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_all),5)}')
print(f'standard deviation = {round(np.std(intra_all),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_all),5)} @ freq {round(tfr.freqs[np.argmax(intra_all)],2)}')
print()

Pair202: Mean ISPC(inter) = 0.25818
Pair202: standard deviation = 0.00516
Pair202: Peak ISPC(inter) 0.26837 @ freq 4.0

Pair202: Mean ISPC(intra) = 0.4702
Pair202: standard deviation = 0.02375
Pair202: Peak ISPC(intra) 0.51428 @ freq 8.59

Pair203: Mean ISPC(inter) = 0.25921
Pair203: standard deviation = 0.00735
Pair203: Peak ISPC(inter) 0.27555 @ freq 11.08

Pair203: Mean ISPC(intra) = 0.48032
Pair203: standard deviation = 0.02965
Pair203: Peak ISPC(intra) 0.536 @ freq 4.0

Pair204: Mean ISPC(inter) = 0.2574
Pair204: standard deviation = 0.00475
Pair204: Peak ISPC(inter) 0.27327 @ freq 4.0

Pair204: Mean ISPC(intra) = 0.47855
Pair204: standard deviation = 0.02402
Pair204: Peak ISPC(intra) 0.51443 @ freq 8.59

Pair205: Mean ISPC(inter) = 0.25881
Pair205: standard deviation = 0.00677
Pair205: Peak ISPC(inter) 0.27919 @ freq 4.0

Pair205: Mean ISPC(intra) = 0.48772
Pair205: standard deviation = 0.02246
Pair205: Peak ISPC(intra) 0.51993 @ freq 6.66

Pair206: Mean ISPC(inter) = 0.25972
Pai

Mean ISPC(inter) = 0.25789
standard deviation = 0.00443
Peak ISPC(inter) 0.27075 @ freq 4.0

Mean ISPC(intra) = 0.4761
standard deviation = 0.0228
Peak ISPC(intra) 0.51115 @ freq 4.0



In [8]:
print(f'Mean ISPC(inter) = {round(np.mean(inter_all),5)}')
print(f'standard deviation = {round(np.std(inter_all),5)}')
print(f'Peak ISPC(inter) {round(np.max(inter_all),5)} @ freq {round(tfr.freqs[np.argmax(inter_all)],2)}')
print(f'Peak ISPC(inter) {round(np.min(inter_all),5)} @ freq {round(tfr.freqs[np.argmin(inter_all)],2)}')
print()

print(f'Mean ISPC(intra) = {round(np.mean(intra_all),5)}')
print(f'standard deviation = {round(np.std(intra_all),5)}')
print(f'Peak ISPC(intra) {round(np.max(intra_all),5)} @ freq {round(tfr.freqs[np.argmax(intra_all)],2)}')
print(f'Peak ISPC(intra) {round(np.min(intra_all),5)} @ freq {round(tfr.freqs[np.argmin(intra_all)],2)}')

print()




Mean ISPC(inter) = 0.25789
standard deviation = 0.00443
Peak ISPC(inter) 0.27075 @ freq 4.0
Peak ISPC(inter) 0.25327 @ freq 14.3

Mean ISPC(intra) = 0.4761
standard deviation = 0.0228
Peak ISPC(intra) 0.51115 @ freq 4.0
Peak ISPC(intra) 0.44861 @ freq 34.88



In [9]:
from scipy.stats import mannwhitneyu

stat, p = mannwhitneyu(inter_all,intra_all)
print('Statistics=%.3f, p=%.3f' % (stat, p))
# interpret
alpha = 0.05
if p > alpha:
	print('Same distribution (fail to reject H0)')
else:
    print('Different distribution (reject H0)')

Statistics=0.000, p=0.000
Different distribution (reject H0)


In [10]:
from scipy.stats import shapiro

shapiro(inter_all)

ShapiroResult(statistic=0.8512512445449829, pvalue=0.005594305694103241)

# Diff: ISPC Inter

In [11]:
plt.figure(figsize=(10,6),dpi=1200)

# interbrain
inter_diff = []
#initialization of result list
zip_object = zip(inter_early, inter_late)
for a,b in zip_object:
    inter_diff.append(a-b)
    

# plot    
plt.plot(tfr.freqs, inter_diff, c=p_red, lw=3, ls='--')

#cosmetics
plt.title('Diff: Early vs. late ISPC of all pairs and all trials - interbrain')
plt.ylim(-.05,.1)
plt.xlabel('frequency')
plt.ylabel('ISPC')  
plt.axhline(y=0, c='k', ls='dotted')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

print(f'Mean diff = {round(np.mean(inter_diff),5)}')
print(f'standard deviation = {round(np.std(inter_diff),5)}')
print(f'Peak diff {round(np.max(inter_diff),5)} @ freq {round(tfr.freqs[np.argmax(inter_diff)],2)}')

Mean diff = 0.00156
standard deviation = 0.00159
Peak diff 0.00451 @ freq 4.54


In [12]:
plt.figure(figsize=(10,6),dpi=1200)
# plot difference between early and late for each pair (inter brain)
for pair in ['202','203','204','205','206','207','208','209','211','212']:
    ispcs_early_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_early.mat"))["early"]
    avg_ispcs_early_pairs = np.mean(ispcs_early_pairs, axis=0)
    ispcs_late_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_late.mat"))["late"]
    avg_ispcs_late_pairs = np.mean(ispcs_late_pairs, axis=0)

    inter_early_pairs = [np.mean(avg_ispcs_early_pairs[0:64, 64:2*64, i]) for i in range(avg_ispcs_early_pairs.shape[2])]
    inter_late_pairs = [np.mean(avg_ispcs_late_pairs[0:64, 64:2*64, i]) for i in range(avg_ispcs_late_pairs.shape[2])]

    
    # get diffwave for each pair
    inter_diff_pairs = []
    zip_object = zip(inter_early_pairs, inter_late_pairs)
    for list1_i, list2_i in zip_object:
        inter_diff_pairs.append(list1_i-list2_i)
        
    print(f'Pair{pair}: Mean diff = {round(np.mean(inter_diff_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(inter_diff_pairs),5)}')
    print(f'Pair{pair}: Peak diff {round(np.max(inter_diff_pairs),5)} @ freq {round(tfr.freqs[np.argmax(inter_diff_pairs)],2)}')
    print()

    # plot
    plt.plot(tfr.freqs, inter_diff_pairs,label=pair, alpha=0.4, ls='--')

# plot mean
plt.plot(tfr.freqs, inter_diff, lw=3, c=p_red, label='mean', ls='--')    
    
# cosmetics
plt.legend()
plt.title('Diff: Early vs. late ISPCS of each pair over all trials - interbrain')
plt.ylim(-.05,.1)
plt.xlabel('frequency')
plt.ylabel('ISPC') 
plt.axhline(y=0, c='k', ls='dotted')


# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

Pair202: Mean diff = 0.00059
Pair202: standard deviation = 0.00433
Pair202: Peak diff 0.01019 @ freq 4.0

Pair203: Mean diff = 0.00164
Pair203: standard deviation = 0.00481
Pair203: Peak diff 0.00858 @ freq 7.56

Pair204: Mean diff = 0.00215
Pair204: standard deviation = 0.00372
Pair204: Peak diff 0.00911 @ freq 4.54

Pair205: Mean diff = 0.00458
Pair205: standard deviation = 0.00764
Pair205: Peak diff 0.01788 @ freq 5.86

Pair206: Mean diff = 0.00092
Pair206: standard deviation = 0.0061
Pair206: Peak diff 0.01311 @ freq 11.08

Pair207: Mean diff = 0.00386
Pair207: standard deviation = 0.00605
Pair207: Peak diff 0.01725 @ freq 20.95

Pair208: Mean diff = -0.00091
Pair208: standard deviation = 0.00468
Pair208: Peak diff 0.00787 @ freq 11.08

Pair209: Mean diff = 0.00078
Pair209: standard deviation = 0.00306
Pair209: Peak diff 0.00455 @ freq 16.24

Pair211: Mean diff = 0.00215
Pair211: standard deviation = 0.00339
Pair211: Peak diff 0.00713 @ freq 39.62

Pair212: Mean diff = 0.00265
Pair

# Diff: ISPC Intra

In [13]:
plt.figure(figsize=(10,6),dpi=1200)

# intrabrain
intra_diff = []
#initialization of result list
zip_object = zip(intra_early, intra_late)
for a,b in zip_object:
    intra_diff.append(a-b)

# plot
plt.plot(tfr.freqs, intra_diff, c=p_red, lw=3)

# cosmetis
plt.title('Diff: Early vs. late ISPC of all pairs and all trials')
plt.ylim(-.05,.1)
plt.xlabel('frequency')
plt.ylabel('ISPC')  
plt.axhline(y=0, c='k', ls='dotted')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

print(f'Mean diff = {round(np.mean(intra_diff),5)}')
print(f'standard deviation = {round(np.std(intra_diff),5)}')
print(f'Peak diff {round(np.max(intra_diff),5)} @ freq {round(tfr.freqs[np.argmax(intra_diff)],2)}')

Mean diff = 0.00197
standard deviation = 0.00144
Peak diff 0.00426 @ freq 11.08


In [ ]:
plt.figure(figsize=(10,6),dpi=1200)
# plot difference between early and late for each pair (intra brain)
for pair in ['202','203','204','205','206','207','208','209','211','212']:
    ispcs_early_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_early.mat"))["early"]
    avg_ispcs_early_pairs = np.mean(ispcs_early_pairs, axis=0)
    ispcs_late_pairs = loadmat(op.join(result_dir, "ispc_matrices", str(pair) + "_late.mat"))["late"]
    avg_ispcs_late_pairs = np.mean(ispcs_late_pairs, axis=0)

    intra_early_pairs = [np.mean(avg_ispcs_early_pairs[0:64, 0:64, i]) for i in range(avg_ispcs_early_pairs.shape[2])]
    
    intra_late_pairs = [np.mean(avg_ispcs_late_pairs[0:64, 0:64, i]) for i in range(avg_ispcs_late_pairs.shape[2])]

    
    
    # get diffwave for each pair
    intra_diff_pairs = []
    zip_object = zip(intra_early_pairs, intra_late_pairs)
    for list1_i, list2_i in zip_object:
        intra_diff_pairs.append(list1_i-list2_i)
        
    print(f'Pair{pair}: Mean diff = {round(np.mean(intra_diff_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(intra_diff_pairs),5)}')
    print(f'Pair{pair}: Peak diff {round(np.max(intra_diff_pairs),5)} @ freq {round(tfr.freqs[np.argmax(intra_diff_pairs)],2)}')
    print()
    
    # plot
    plt.plot(tfr.freqs, intra_diff_pairs,label=pair, alpha=0.4)

# plot mean
plt.plot(tfr.freqs, intra_diff, c=p_red, lw=3, label='mean')

    
# cosmetics
plt.legend()
plt.title('Diff: Early vs. late ISPCS of each pair over all trials - intrabrain')
plt.ylim(-.05,.1)
plt.xlabel('frequency')
plt.ylabel('ISPC') 
plt.axhline(y=0, c='k', ls='dotted')

# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks([float(i) for i in labels[0::4]], labels[0::4])

plt.show()

Pair202: Mean diff = 0.00211
Pair202: standard deviation = 0.00242
Pair202: Peak diff 0.00582 @ freq 34.88

Pair203: Mean diff = 0.00241
Pair203: standard deviation = 0.00475
Pair203: Peak diff 0.01016 @ freq 16.24

Pair204: Mean diff = -0.00166
Pair204: standard deviation = 0.00503
Pair204: Peak diff 0.00676 @ freq 16.24

Pair205: Mean diff = -0.00245
Pair205: standard deviation = 0.00761
Pair205: Peak diff 0.01427 @ freq 45.0

Pair206: Mean diff = 0.00588
Pair206: standard deviation = 0.00665
Pair206: Peak diff 0.01742 @ freq 7.56

Pair207: Mean diff = 0.00064
Pair207: standard deviation = 0.00908
Pair207: Peak diff 0.02076 @ freq 11.08

Pair208: Mean diff = 0.0006
Pair208: standard deviation = 0.0052
Pair208: Peak diff 0.01411 @ freq 4.0



# SWI

In [ ]:
plt.figure(figsize=(10,6),dpi=1200)

pair = '202'
cond = "early"
SWI_early = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_" + cond + ".mat"))[cond]

print(f'Pair{pair}: Mean SWI = {round(np.mean(np.mean(SWI_early, axis=0)),5)}')
print(f'Pair{pair}: standard deviation = {round(np.std(np.mean(SWI_early, axis=0)),5)}')
print(f'Pair{pair}: Peak SWI {round(np.max(np.mean(SWI_early, axis=0)),5)} \
      @ freq {round(tfr.freqs[np.argmax(np.mean(SWI_early, axis=0))],2)}')
print()

plt.plot(tfr.freqs, np.mean(SWI_early, axis=0), label=pair)

for pair in ['203','204','205','206','207','208','209','211','212']:
    SWI_pair_early = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_" + cond + ".mat"))[cond]
    SWI_early = np.concatenate((SWI_early,SWI_pair_early)) 
    
    print(f'Pair{pair}: Mean SWI = {round(np.mean(np.mean(SWI_pair_early, axis=0)),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(np.mean(SWI_pair_early, axis=0)),5)}')
    print(f'Pair{pair}: Peak SWI {round(np.max(np.mean(SWI_pair_early, axis=0)),5)} \
          @ freq {round(tfr.freqs[np.argmax(np.mean(SWI_pair_early, axis=0))],2)}')
    print()
    
    
    # plot SWI over all trials
    plt.plot(tfr.freqs, np.mean(SWI_pair_early, axis=0), label=pair, alpha=0.3)

# get avg over pairs             
avg_SWI_early = np.mean(SWI_early, axis=0)

print(f'Mean SWI = {round(np.mean(avg_SWI_early),5)}')
print(f'standard deviation = {round(np.std(avg_SWI_early),5)}')
print(f'Peak SWI {round(np.max(avg_SWI_early),5)} @ freq {round(tfr.freqs[np.argmax(avg_SWI_early)],2)}')

# plot mean
plt.plot(tfr.freqs, avg_SWI_early, label='mean', lw=3, c=p_blue) 


# cosmetics
plt.legend()
plt.title('Early SWI over pairs')
plt.ylim(0,.15)
plt.xlabel('frequency')
plt.ylabel('SWI')  

# log scale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

In [ ]:
plt.figure(figsize=(10,6),dpi=1200)

pair = '202'
cond = "late"
SWI_late = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_" + cond + ".mat"))[cond]

print(f'Pair{pair}: Mean SWI = {round(np.mean(np.mean(SWI_late, axis=0)),5)}')
print(f'Pair{pair}: standard deviation = {round(np.std(np.mean(SWI_late, axis=0)),5)}')
print(f'Pair{pair}: Peak SWI {round(np.max(np.mean(SWI_late, axis=0)),5)} \
      @ freq {round(tfr.freqs[np.argmax(np.mean(SWI_late, axis=0))],2)}')
print()

plt.plot(tfr.freqs, np.mean(SWI_late, axis=0), label=pair)

for pair in ['203','204','205','206','207','208','209','211','212']:
    SWI_pair_late = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_" + cond + ".mat"))[cond]
    SWI_late = np.concatenate((SWI_late,SWI_pair_late)) 
    
    # plot SWI over all trials
    plt.plot(tfr.freqs, np.mean(SWI_pair_late, axis=0), label=pair, alpha=0.4)
    
    print(f'Pair{pair}: Mean SWI = {round(np.mean(np.mean(SWI_pair_late, axis=0)),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(np.mean(SWI_pair_late, axis=0)),5)}')
    print(f'Pair{pair}: Peak SWI {round(np.max(np.mean(SWI_pair_late, axis=0)),5)} \
          @ freq {round(tfr.freqs[np.argmax(np.mean(SWI_pair_late, axis=0))],2)}')
    print()

# get avg over pairs             
avg_SWI_late = np.mean(SWI_late, axis=0)

print(f'Mean SWI = {round(np.mean(avg_SWI_late),5)}')
print(f'standard deviation = {round(np.std(avg_SWI_late),5)}')
print(f'Peak SWI {round(np.max(avg_SWI_late),5)} @ freq {round(tfr.freqs[np.argmax(avg_SWI_late)],2)}')

# plot mean
plt.plot(tfr.freqs, avg_SWI_late, label='mean', lw=3, c=p_yellow) 


# cosmetics
plt.legend()
plt.title('Late SWI over pairs')
plt.ylim(0,.15)
plt.xlabel('frequency')
plt.ylabel('SWI')  

# log scale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

# Diff: SWI 

In [ ]:
plt.figure(figsize=(10,6),dpi=1200)

diff_SWI = []
#initialization of result list
zip_object = zip(avg_SWI_early, avg_SWI_late)
for a,b in zip_object:
    diff_SWI.append(a-b)

# plot
plt.plot(tfr.freqs, diff_SWI, c=p_red, lw=3)

# cosmetis
plt.title('Diff: Early vs. late SWI of all pairs and all trials')
plt.ylim(-.005,.01)
plt.xlabel('frequency')
plt.ylabel('SWI')  
plt.axhline(y=0, c='k', ls='dotted')


# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()
print(f'Mean diff = {round(np.mean(diff_SWI),5)}')
print(f'standard deviation = {round(np.std(diff_SWI),5)}')
print(f'Peak diff {round(np.max(diff_SWI),5)} @ freq {round(tfr.freqs[np.argmax(diff_SWI)],2)}')

In [ ]:
plt.figure(figsize=(10,6),dpi=1200)
# plot difference between early and late for each pair (inter brain)
for pair in ['202','203','204','205','206','207','208','209','211','212']:
    SWI_early_pairs = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_early.mat"))["early"]
    avg_SWI_early_pairs = np.mean(SWI_early_pairs, axis=0)
    SWI_late_pairs = loadmat(op.join(result_dir, "small_worlds", str(pair) + "_late.mat"))["late"]
    avg_SWI_late_pairs = np.mean(SWI_late_pairs, axis=0)

    
    # get diffwave for each pair
    SWI_diff_pairs = []
    zip_object = zip(avg_SWI_early_pairs, avg_SWI_late_pairs)
    for a, b in zip_object:
        SWI_diff_pairs.append(a-b)
   
    print(f'Pair{pair}: Mean diff = {round(np.mean(SWI_diff_pairs),5)}')
    print(f'Pair{pair}: standard deviation = {round(np.std(SWI_diff_pairs),5)}')
    print(f'Pair{pair}: Peak diff {round(np.max(SWI_diff_pairs),5)} @ freq {round(tfr.freqs[np.argmax(SWI_diff_pairs)],2)}')
    print()
    
    # plot
    plt.plot(tfr.freqs, SWI_diff_pairs,label=pair, alpha=0.4)

# plot mean
plt.plot(tfr.freqs, diff_SWI, lw=3, c=p_red, label='mean diff')    
    
# cosmetics
plt.legend()
plt.title('Difference: Early vs. late SWI of each pair over all trials')
plt.ylim(-.005,.01)
plt.xlabel('frequency')
plt.ylabel('SWI') 
plt.axhline(y=0, c='k', ls='dotted')


# logscale
labels = [str(round(i,2)) for i in tfr.freqs]
labels.append('45')
plt.xscale('log',subs=[4])
plt.xticks( [float(i) for i in labels[0::4]] , labels[0::4])

plt.show()

print(f'Mean diff = {round(np.mean(diff_SWI),5)}')
print(f'standard deviation = {round(np.std(diff_SWI),5)}')
print(f'Peak diff {round(np.max(diff_SWI),5)} @ freq {round(tfr.freqs[np.argmax(diff_SWI)],2)}')